In [0]:
#Importing necessary library
from pyspark.sql import SparkSession
from pyspark.sql.types import *
from pyspark.ml.feature import Word2Vec
from pyspark.ml.clustering import KMeans
from pyspark.ml.evaluation import ClusteringEvaluator
import matplotlib.pyplot as plt
import pandas as pd

In [0]:
#Initiating spark session
spark = SparkSession.builder.config('spark.sql.parquet.binaryAsString', 'true') \
            .config('spark.jars.packages', 'org.mongodb.spark:mongo-spark-connector_2.12:3.0.1')\
            .appName("OMS_lyrics") \
            .getOrCreate()

aws_access_key = 'ACCESS_ID'
aws_secret_key = 'SECRET'
spark._jsc.hadoopConfiguration().set('spark.jars.packages', 'org.apache.hadoop:hadoop-aws:3.3.1')
spark._jsc.hadoopConfiguration().set("spark.hadoop.fs.s3a.impl", "org.apache.hadoop.fs.s3a.S3AFileSystem")
spark._jsc.hadoopConfiguration().set("fs.s3a.access.key", aws_access_key)
spark._jsc.hadoopConfiguration().set("fs.s3a.secret.key", aws_secret_key)
spark._jsc.hadoopConfiguration().set('spark.network.timeout','7200s')
spark._jsc.hadoopConfiguration().set('spark.executor.heartbeatInterval','7200s')

**Note:** Below cells are for merging clustering results with other workflow results for our SpotFlix website for recommending songs to users

In [0]:
# Read million song dataset
songs_df = spark.read.parquet("s3a://million-song-dataset-16/data")

# Select columns relevant to the genre detection task
selected_columns =['song_id','track_id']
songs_df2 =songs_df.select(*selected_columns)
songs_df2.display()

song_id track_id U09BUUhJTTEyQThDMTNDQkIw VFJUQklSUzEyOEY0Mjg0OUQy U09LSExEUDEyQUIwMTg3RkUz VFJUQklMWDEyOTAzQ0YzNkYz U09HRFVYUDEyQTZENEYzRjk4 VFJUQklFSDEyOEY0MjdDMTND U09HT0FIWTEyQThDMTM4QTc5 VFJUQklFRDEyOEY0MjY4RTBD U09ISkJIVjEyQUIwMTgzQ0ZD VFJUQklaWDEyOEY5MzJBNUU0 U09MU0RTRTEyQUIwMTgyODhG VFJUQklQSzEyOTAzQ0FDOTYx U09WS01FRDEyQThDMTNDMzBF VFJUQklTQzEyOEY0MkFCNDJF U09MWFZRQzEyQTU4QTdDMTRB VFJUQklTUjEyOEY5MkREQzM2 U09ZQk9FRTEyQUM0Njg5RTE4 VFJUQklKRDEyOTAzRDBFRjBE U09LSExYTjEyQUM0Njg3OEIz VFJUQklRWDEyOTAzQ0VENzVG U09NSVZXVTEyQThDMTQzMDUw VFJUQklZUjEyOEY5MzBBNjkw U09ISU5RRjEyQTU4QTc3NTg1 VFJUQklLWTEyOEY0MkIyMTM5 U09MSUNZTTEyQTU4QTdDQkM3 VFJUQklIWTEyOEY0MjU4MUJF U09JT1pJRTEyQTU4QTdGRjFG VFJUQklIUjEyOEVGMzVGNDU0 U09BSlVETjEyQThDMTNEQTYy VFJUQklOWTEyOEY0MjlDODc2 U09EUU1VUjEyQTZENEZEQjFE VFJUQklOSjEyOEY0MjRCMzQw U09WWFFRTjEyQUIwMTgyOTJC VFJUQklQTTEyOEY5MkY5MkZE U09IREtRTTEyQThBRTQ2MDNF VFJUQklVSzEyOEY0MjU5OUIx U09WQUZBSjEyQThDMTM2NzAx VFJUQklQTzEyOTAzQ0I1Q0M3 U09LSlRZSTEyQTZENEZCMEY4 VFJUQkZPWDEyOEY5MzI2REFG U09YVUxLRzEyQUM0NjhENUI4 VFJUQkZaTTEyOTAzQ0VDNkEw U09UUENDTTEyQUIwMTg1MjVD VFJUQkZLUDEyOEY5MkY3Qzg5 U09TSEdLSjEyQThDMTNDOUE5 VFJUQkZSUjEyOEY0MjlBMzhG U09XQUxZRTEyQUFGM0IyRDcy VFJUQkZUQzEyOEY5MkY2MzZC U09QRERPVTEyQUIwMTg4QkVD VFJUQkZMVDEyOEY5MzNCMzY4 U09CWEVCSzEyQUIwMTgwMkQ2 VFJUQkZXWTEyOEY5MkU2MjQx U09GTkNVRTEyQTZENEZBNkY5 VFJUQkZOVzEyOEYxNDg3RTJG U09TU1lYWTEyQTZENEY4RkI2 VFJUQkZHRjEyOEYxNDgyRTg2 U09DTkdSSTEyQThDMTNBNzE0 VFJUQkZFTzEyOEY0MjcxRUU1 U09RQk9XVjEyQUIwMTgyNTAx VFJUQkZERDEyOEY5MzREODZE U09RTUVPWTEyQThDMTQyRUZF VFJUQkZNUjEyOEY5MkQzREI1 U09SWkJTTTEyQTY3MDFFMUIz VFJUQkZCRTEyOEUwNzg3M0M3 U09KR1pUQzEyQTU4QTdDMjJD VFJUQkZBQzEyOEY5MzIzN0JE U09JUE5ERzEyQTZCRDU2QkJC VFJUQkZEQTEyOEVGMzRDM0Mz U09CTE1XQzEyQUY3MkE3NjlB VFJUQkZXSzEyOEY5MzU1NUM3 U09UVkFRRDEyQUIwMTgxQTI4 VFJUQkZYUTEyOEY5MzJCRDZD U09UQkxPWTEyQTZENEZCMjVD VFJUQkZRRzEyOEYxNEEzNUVE U09NQVVWUDEyQTY3QURFNzNB VFJUQkZXTzEyOEUwNzk4Q0Uy U09HVUZJTjEyQUM0Njg4NTQ2 VFJUQkZEUDEyOTAzQ0ZFOTZD U09OWEpUSDEyQUFGM0IxRUZD VFJUQkZPVDEyOEY5MkYwQUM4 U09WTFhGUDEyQThDMTQyMTQ2 VFJUQkZJVDEyOEY0MjkwRDAz U09DSEZHRTEyQThDMTQzOTFB VFJUQkZQTTEyOEY5MkQxQTU3 U09EVFZESTEyQUIwMTgzQkYz VFJUQkZCSjEyOEY5MzEzNUIy U09LUk1aTDEyQTY3QURDODdF VFJUQkZLWjEyOEVGMzNEQkQy U09LUExPVTEyQUIwMTgxRDU1 VFJUQkZCRjEyOTAzQ0IwRTRC U09UR1FQVjEyQThDMTQ1MjE3 VFJUQkZBQjEyOEY5MkQwRDZF U09CUFVYSjEyQThDMTM4Njg0 VFJUQkZNTjEyOEY0MjYyMTFB U09ZS0ZUVjEyQThDMTMyNTdB VFJUQkZUUDEyOEY0MjcxQjcw U09HU1dUSTEyQThDMTM3Q0My VFJUQkZLQzEyOEY0MjVCN0Mz U09DTVlVWDEyQUIwMTg2MkUz VFJUQkZDSTEyOEY5MzRGREIw U09WV1BFVjEyQTU4QTdCQjU1 VFJUQkZHSzEyOEY0MjVCRUU2 U09VQ0tPSDEyQThDMTM5NUQ1 VFJUQkZXQjEyOTAzQ0VGOTQ1 U09aWU9BRTEyQUY3MkExMUZG VFJUQkZBSjEyOEY5MkU3M0NB U09RTE5DQjEyQUIwMTgzMzlE VFJUQkZOVzEyOEY5MzFGNUM0 U09LUE9RUTEyQThDMTNFM0VF VFJUQkZTSjEyOEY0MkIxMTcy U09EUFlGTDEyQThDMTM5RUU4 VFJUQkZBSjEyOEY0MjcxRkE5 U09KVEdWRjEyQTZENEZENTY1 VFJUQkZBUzEyOEY0MjQzQjBB U09FSFJQSjEyQUIwMTg4NzA3 VFJUQkZSQTEyOTAzQzk0NEJE U09PRFZKQzEyQUMzREY2RDgz VFJUQkZOUDEyOTAzQ0U2RTlF U09PUlhBSTEyQThDMTM0RDBD VFJUQkZTVTEyOEY0MjRBRDUw U09GVlpJQzEyQTU4QTdCNjQ4 VFJUQkZZRTEyOEY0MjUwNjcy U09BS1VQVzEyQUIwMTgzNDZG VFJUQkZURTEyOEY5MzFDMzUy U09MWVFOUjEyQTU4QTgxRUI4 VFJUQkZUVzEyOEY5MzAzNkRG U09BS0REUzEyQUIwMTdDNDNB VFJUQkZBSTEyOEY5MkYyQzBF U09YVUZaRDEyQThDMTQxQUU1 VFJUQkZJSzEyOEY5MkUxNDNE U09RS0FYTDEyQUIwMTg0Nzk2 VFJUQkZOSTEyOEY5MzA4NzhE U09XREZLVDEyQUIwMTg0ODA3 VFJUQkZBTDEyOEY5MzIyRDBC U09ZVEpUQjEyQUIwMTg0N0NE VFJUQkZWRjEyOEY5MzAwMDMw U09WVk9GWjEyQTZENEY3MUYx VFJUQkZFTzEyOTAzQ0I2OUQz U09MVlZLTjEyQUIwMTg0OEFF VFJUQkZJUTEyOTAzQzlENDVE U09XWEJDVDEyQUIwMTdERDNC VFJUQkZDTTEyOEY5MkZGRDdG U09ZUVVTWjEyQThDMTM2RDBD VFJUQkZNQzEyOEY0MjY2NEVG U09TTlBBWDEyQUM0NjhDMDhD VFJUQkZFRDEyOTAzQ0U1RkI5 U09TUldISDEyQUM0Njg1NkFC VFJUQkZaVDEyOTAzQ0VGNzY3 U09TV01IRTEyQThDMTMxRERF VFJUQkZLVDEyOEY0MjYzRUZG U09aV1ZIUjEyQUM0NjhCOTM1 VFJUQkZVQzEyOTAzRDA1QjY3 U09BVFZTQjEyQ0Y1Rjg2QkNE VFJUQkZaSDEyOEY5MkU1NENC U09PSk9OSzEyQUIwMTdGNzgy VFJUQkZOQzEyOEY5MzBCNzM4 U09FSlRNTDEyQThDMTNBRDU0 VFJUQkZNTTEyOEY0MjY0NUZB U09MQlVQUTEyQTZENEZBMzI1 VFJUQlJO

In [0]:
df_pred = predictions.join(songs_df2,['track_id'],how='inner')
df_pred.display()

track_id words features prediction song_id TRAAAHZ128E0799171 List(i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, you, you, you, you, you, you, you, you, you, you, to, to, to, to, to, to, to, to, to, to, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, a, a, a, a, a, a, a, a, a, a, a, a, a, a, a, a, a, a, a, a, a, me, it, it, it, it, it, it, it, it, it, it, it, it, it, it, it, it, it, it, it, it, not, not, not, not, not, not, not, not, not, not, not, in, in, in, in, in, in, in, in, in, in, in, in, my, my, my, my, my, my, my, my, my, is, is, is, is, is, is, is, is, is, is, of, of, of, of, of, of, of, of, of, your, that, that, that, that, that, do, do, do, do, do, do, do, do, do, do, do, on, on, on, on, are, we, am, am, am, am, am, am, am, am, am, am, am, am, am, am, am, am, am, all, all, all, all, all, all, all, for, for, for, for, no, have, have, love, love, so, so, so, so, so, know, this, this, this, this, this, this, but, but, but, but, but, with, with, with, with, what, what, when, like, now, now, now, now, now, now, now, now, time, time, can, can, can, come, come, go, up, up, up, up, up, up, up, up, up, up, up, one, one, one, one, one, one, one, one, one, one, one, one, one, one, one, one, they, out, out, down, down, get, get, get, get, get, get, was, was, was, was, see, see, see, got, got, never, from, feel, want, want, want, want, way, say, say, as, as, as, ca, at, at, yeah, yeah, yeah, yeah, yeah, yeah, yeah, back, back, back, heart, here, night, night, need, look, look, world, world, more, caus, caus, caus, right, been, tell, man, man, man, live, again, give, too, onli, onli, onli, onli, onli, onli, onli, onli, onli, onli, onli, whi, dream, around, good, good, about, about, about, some, some, some, some, over, leav, had, gone, stay, god, these, new, him, stop, stop, burn, burn, burn, sun, off, play, made, made, start, hard, hard, hard, boy, put, name, same, fuck, other, rememb, star, yes, real, real, real, two, two, two, black, rock, shine, heaven, work, work, big, big, big, big, big, big, street, came, till, deep, happi, ai, ai, ai, best, listen, hell, set, em, em, em, pass, fool, fool, fool, fool, fool, fool, chanc, part, nobodi, game, game, though, each, young, readi, shit, shit, shit, along, hit, happen, whole, car, pray, gave, tire, lot, sinc, kid, nigga, nigga, nigga, nigga, hot, bright, secret, push, push, three, three, three, drop, wear, uh, uh, thank, catch, fell, top, top, top, cover, write, number, number, number, lock, bless, bless, knock, four, four, four, check, check, famili, choos, small, wit, swear, yall, c, kept, kept, busi, price, trip, shoulder, tune, tune, tune, pop, pop, wife, bite, bite, bite, west, block, g, g, g, g, g, g, g, direct, direct, rap, rap, laid, clock, paid, yellow, judg, doubl, doubl, doubl, doubl, doubl, doubl, wise, mom, older, motherfuck, motherfuck, motherfuck, spot, beach, aw, aw, aw, aw, throne, steadi, handl, coast, mic, mic, boss, weed, presenc, presenc, jail, grind, buck, buck, buck, buck, buck, buck, buck, buck, buck, buck, buck, buck, buck, righteous, sharp, playa, famous, colder, file, local, process, bid, profit) Map(vectorType -> dense, length -> 10, values -> List(0.3147820885135577, 0.31298801836772605, -0.1373848327446299, -0.11560719789220737, -0.10198442004621029, -0.00367037882311986, -0.03769019453571393, -0.26109189989116904, -0.3201856662075107, -0.4151620184458219)) 32 U09BUEVSSDEyQTU4QTc4N0RD TRAABLR128F423B7E3 List(i, i, i, i, i, i, i, i, i, i, i, the, the, the, the, the, you, you, you, you, you, you, to, to, to, and, and, and, and, and, and, and, and, and, and, a, a, a, a, a, a, me, me, me, me, me, me, it, it, it, it, it, it, it, not, in, in, in, my, 

In [0]:
#Saving intermediate results to table
df_pred.select('track_id','song_id','prediction').write.mode("overwrite").saveAsTable("default.kmeans_predictions_100")

In [0]:
df_pred = spark.read.table("default.kmeans_predictions_100") 

In [0]:
df_pred.count()

Out[2]: 210519

In [0]:
df_pred.display()

track_id words features prediction song_id TRAAAHZ128E0799171 List(i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, the, you, you, you, you, you, you, you, you, you, you, to, to, to, to, to, to, to, to, to, to, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, a, a, a, a, a, a, a, a, a, a, a, a, a, a, a, a, a, a, a, a, a, me, it, it, it, it, it, it, it, it, it, it, it, it, it, it, it, it, it, it, it, it, not, not, not, not, not, not, not, not, not, not, not, in, in, in, in, in, in, in, in, in, in, in, in, my, my, my, my, my, my, my, my, my, is, is, is, is, is, is, is, is, is, is, of, of, of, of, of, of, of, of, of, your, that, that, that, that, that, do, do, do, do, do, do, do, do, do, do, do, on, on, on, on, are, we, am, am, am, am, am, am, am, am, am, am, am, am, am, am, am, am, am, all, all, all, all, all, all, all, for, for, for, for, no, have, have, love, love, so, so, so, so, so, know, this, this, this, this, this, this, but, but, but, but, but, with, with, with, with, what, what, when, like, now, now, now, now, now, now, now, now, time, time, can, can, can, come, come, go, up, up, up, up, up, up, up, up, up, up, up, one, one, one, one, one, one, one, one, one, one, one, one, one, one, one, one, they, out, out, down, down, get, get, get, get, get, get, was, was, was, was, see, see, see, got, got, never, from, feel, want, want, want, want, way, say, say, as, as, as, ca, at, at, yeah, yeah, yeah, yeah, yeah, yeah, yeah, back, back, back, heart, here, night, night, need, look, look, world, world, more, caus, caus, caus, right, been, tell, man, man, man, live, again, give, too, onli, onli, onli, onli, onli, onli, onli, onli, onli, onli, onli, whi, dream, around, good, good, about, about, about, some, some, some, some, over, leav, had, gone, stay, god, these, new, him, stop, stop, burn, burn, burn, sun, off, play, made, made, start, hard, hard, hard, boy, put, name, same, fuck, other, rememb, star, yes, real, real, real, two, two, two, black, rock, shine, heaven, work, work, big, big, big, big, big, big, street, came, till, deep, happi, ai, ai, ai, best, listen, hell, set, em, em, em, pass, fool, fool, fool, fool, fool, fool, chanc, part, nobodi, game, game, though, each, young, readi, shit, shit, shit, along, hit, happen, whole, car, pray, gave, tire, lot, sinc, kid, nigga, nigga, nigga, nigga, hot, bright, secret, push, push, three, three, three, drop, wear, uh, uh, thank, catch, fell, top, top, top, cover, write, number, number, number, lock, bless, bless, knock, four, four, four, check, check, famili, choos, small, wit, swear, yall, c, kept, kept, busi, price, trip, shoulder, tune, tune, tune, pop, pop, wife, bite, bite, bite, west, block, g, g, g, g, g, g, g, direct, direct, rap, rap, laid, clock, paid, yellow, judg, doubl, doubl, doubl, doubl, doubl, doubl, wise, mom, older, motherfuck, motherfuck, motherfuck, spot, beach, aw, aw, aw, aw, throne, steadi, handl, coast, mic, mic, boss, weed, presenc, presenc, jail, grind, buck, buck, buck, buck, buck, buck, buck, buck, buck, buck, buck, buck, buck, righteous, sharp, playa, famous, colder, file, local, process, bid, profit) Map(vectorType -> dense, length -> 10, values -> List(0.3147820885135577, 0.31298801836772605, -0.1373848327446299, -0.11560719789220737, -0.10198442004621029, -0.00367037882311986, -0.03769019453571393, -0.26109189989116904, -0.3201856662075107, -0.4151620184458219)) 32 SOAPERH12A58A787DC TRAADQX128F422B4CF List(i, i, i, i, i, i, i, i, the, the, the, the, you, you, you, you, you, you, you, you, you, you, to, to, to, to, a, me, it, it, it, it, it, not, not, my, my, is, of, of, your, your, that, that, that, are, we, we, we, will, will, will, all, be, be, ha

In [0]:
df_top = spark.read.table('default.df_first_page_final').withColumnRenamed('prediction','popularity_pred')

In [0]:
df_pred_top = df_top.join(df_pred, 'song_id', how='inner')
df_pred_top.createOrReplaceTempView('pred')

In [0]:
df_pred_top.display()

song_id title popularity_pred user_id play_count genre avg_play_count track_id words features prediction SOJJYDE12AF729FC16 Two Is Better Than One 0.8533525063568872 ffad6a9352f87dbe61482e8a7dbb1bf8cf37c8be 13 Religious 349.0 TRAWVYP128F9305DF2 List(i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, i, the, the, the, the, the, the, the, the, you, you, you, you, you, you, you, you, you, you, you, you, you, you, you, you, you, you, you, to, to, to, to, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, and, me, me, me, it, it, it, it, it, not, not, not, not, my, my, my, my, my, my, my, my, is, is, is, is, is, is, is, is, is, is, of, of, of, of, of, your, your, that, that, that, that, that, that, do, on, on, am, am, am, am, am, all, all, for, be, have, have, have, so, so, so, so, so, know, know, this, but, but, but, with, with, what, what, when, now, now, time, time, time, time, come, come, come, there, there, there, there, one, one, one, one, one, one, one, one, out, out, out, out, out, got, got, got, make, way, way, say, say, take, ca, ca, ca, ca, day, day, babi, away, away, life, life, life, life, life, life, could, look, eye, eye, caus, caus, caus, think, think, think, think, live, live, live, live, noth, said, everi, into, into, face, believ, everyth, everyth, hey, hey, someth, word, much, much, much, much, better, better, better, better, better, better, better, better, left, than, than, than, than, than, than, than, than, thought, thought, hard, without, without, without, without, true, true, true, close, rememb, rememb, rememb, breath, breath, two, two, two, two, two, two, two, two, done, ooh, mayb, mayb, mayb, mayb, mayb, mayb, came, came, roll, first, first, upon, final, rest, rest, rest, rest, alreadi, alreadi, alreadi, okay, drift, figur, figur, figur, figur, figur, undon, undon, undon, wore, wore) Map(vectorType -> dense, length -> 10, values -> List(0.3413808585476067, 0.3693100896300906, -0.06909765674401137, 0.09337324674351741, -0.04390362198069944, -0.047906145655502705, 0.033130041345701376, -0.23857545114548528, -0.2824841511451592, -0.4614143411234274)) 67 SOFBOXR12A6310F0FC God Put A Smile Upon Your Face 0.7563203233419701 98cb9a3feb48d15a8328ce16f1b32609698e11f2 2 RnB 835.0 TRBYFON128E0780C8C List(i, i, i, i, i, i, i, i, i, the, the, the, you, you, you, you, you, you, you, you, you, you, you, you, you, you, to, to, to, to, and, and, and, and, and, a, a, a, a, me, me, it, it, it, it, it, it, it, it, it, not, not, my, my, is, is, is, is, your, your, your, your, your, your, your, your, do, do, do, do, do, do, do, on, on, on, are, are, we, we, we, we, am, am, am, all, have, have, have, know, know, know, when, when, when, when, when, when, when, when, now, now, now, now, time, go, go, go, go, go, oh, out, out, out, out, out, out, down, down, down, from, want, want, way, way, way, say, say, say, say, as, as, as, as, as, as, as, as, as, as, as, as, as, as, as, as, as, as, yeah, yeah, yeah, yeah, where, where, where, where, where, where, where, give, give, too, too, fall, good, good, good, good, good, good, good, good, good, ever, ever, face, face, face, face, god, god, god, god, god, than, than, put, put, put, put, gotta, gotta, mine, mine, mine, mine, mine, mine, mine, mine, mine, na, na, smile, smile, smile, smile, line, line, line, work, work, work, work, work, work, nobodi, nobodi, nobodi, wast, upon, upon, upon, upon, guess, guess, gave, gave, gave, gave, honey, honey, grace, grace, grace, grace, style, style, style, draw, draw, draw, wors, wors, nana, nana, nana, nana) Map(vectorType -> dense, length -> 10, values -> List(0.4225828383838938, 0.561781036727611, -0.17492546471616913, 0.22014869581307134, 0.07913144677877426, 0.01519605703651905, -0.11510100098507058, -0.2218903362931263, -0.23905331491222304, -0.4756943182118477)) 60 SOCBUQK12A8AE48B83 Back Of My Lac' 0.6224586231625813 9ae2abce15efa19998984882900850b927ebf7e1 13 Folk 496.0 TRBYLRP128F4255813 List(i, i, i, i, i, i, i, i, i,

In [0]:
#Setting top users from genre based data to their closest clusters based on songs with highest play count for the representative users
df_pred_cluster = spark.sql('select user_id, prediction, song_id, first(features) over(partition by user_id order by play_count desc) as song_feature from pred')
df_pred_cluster.display()

user_id prediction song_id song_feature 296e5769223ae111e530d96c8bcf95fd63d8af9b 9 SOUHTWB12A8C13BA4D Map(vectorType -> dense, length -> 10, values -> List(0.3263355428400712, 0.47665605743726097, -0.3392343500008186, -0.1068093629888235, 0.002029124506486532, -0.025003416654773247, 0.10782888816335262, -0.25724774171622133, -0.46101472043456176, -0.43486737625148053)) 296e5769223ae111e530d96c8bcf95fd63d8af9b 39 SOJNNUA12A8AE48C7A Map(vectorType -> dense, length -> 10, values -> List(0.3263355428400712, 0.47665605743726097, -0.3392343500008186, -0.1068093629888235, 0.002029124506486532, -0.025003416654773247, 0.10782888816335262, -0.25724774171622133, -0.46101472043456176, -0.43486737625148053)) 296e5769223ae111e530d96c8bcf95fd63d8af9b 92 SOPUCYA12A8C13A694 Map(vectorType -> dense, length -> 10, values -> List(0.3263355428400712, 0.47665605743726097, -0.3392343500008186, -0.1068093629888235, 0.002029124506486532, -0.025003416654773247, 0.10782888816335262, -0.25724774171622133, -0.46101472043456176, -0.43486737625148053)) 296e5769223ae111e530d96c8bcf95fd63d8af9b 15 SOXAHKA12AF72A5A65 Map(vectorType -> dense, length -> 10, values -> List(0.3263355428400712, 0.47665605743726097, -0.3392343500008186, -0.1068093629888235, 0.002029124506486532, -0.025003416654773247, 0.10782888816335262, -0.25724774171622133, -0.46101472043456176, -0.43486737625148053)) 296e5769223ae111e530d96c8bcf95fd63d8af9b 67 SOYSCPE12AB0181BBF Map(vectorType -> dense, length -> 10, values -> List(0.3263355428400712, 0.47665605743726097, -0.3392343500008186, -0.1068093629888235, 0.002029124506486532, -0.025003416654773247, 0.10782888816335262, -0.25724774171622133, -0.46101472043456176, -0.43486737625148053)) 296e5769223ae111e530d96c8bcf95fd63d8af9b 48 SONMMKG12A6D4F4661 Map(vectorType -> dense, length -> 10, values -> List(0.3263355428400712, 0.47665605743726097, -0.3392343500008186, -0.1068093629888235, 0.002029124506486532, -0.025003416654773247, 0.10782888816335262, -0.25724774171622133, -0.46101472043456176, -0.43486737625148053)) 296e5769223ae111e530d96c8bcf95fd63d8af9b 39 SOXEHUH12AB018D1E0 Map(vectorType -> dense, length -> 10, values -> List(0.3263355428400712, 0.47665605743726097, -0.3392343500008186, -0.1068093629888235, 0.002029124506486532, -0.025003416654773247, 0.10782888816335262, -0.25724774171622133, -0.46101472043456176, -0.43486737625148053)) 296e5769223ae111e530d96c8bcf95fd63d8af9b 52 SOVDSJC12A58A7A271 Map(vectorType -> dense, length -> 10, values -> List(0.3263355428400712, 0.47665605743726097, -0.3392343500008186, -0.1068093629888235, 0.002029124506486532, -0.025003416654773247, 0.10782888816335262, -0.25724774171622133, -0.46101472043456176, -0.43486737625148053)) 296e5769223ae111e530d96c8bcf95fd63d8af9b 48 SOYMIMI12AB0181E5C Map(vectorType -> dense, length -> 10, values -> List(0.3263355428400712, 0.47665605743726097, -0.3392343500008186, -0.1068093629888235, 0.002029124506486532, -0.025003416654773247, 0.10782888816335262, -0.25724774171622133, -0.46101472043456176, -0.43486737625148053)) 296e5769223ae111e530d96c8bcf95fd63d8af9b 15 SOFLJQZ12A6D4FADA6 Map(vectorType -> dense, length -> 10, values -> List(0.3263355428400712, 0.47665605743726097, -0.3392343500008186, -0.1068093629888235, 0.002029124506486532, -0.025003416654773247, 0.10782888816335262, -0.25724774171622133, -0.46101472043456176, -0.43486737625148053)) 296e5769223ae111e530d96c8bcf95fd63d8af9b 3 SOSXPFU12AB017FE27 Map(vectorType -> dense, length -> 10, values -> List(0.3263355428400712, 0.47665605743726097, -0.3392343500008186, -0.1068093629888235, 0.002029124506486532, -0.025003416654773247, 0.10782888816335262, -0.25724774171622133, -0.46101472043456176, -0.43486737625148053)) 296e5769223ae111e530d96c8bcf95fd63d8af9b 66 SOKYDWK12A6D4F623F Map(vectorType -> dense, length -> 10, values -> List(0.3263355428400712, 0.47665605743726097, -0.3392343500008186, -0.1068093629888235, 0.002029124506486532, -0.025003416654773247, 0.10782888816335262, -0.25724774171622133, -0.46101472

In [0]:
df_popularity = spark.read.table('default.song_popularity_prediction_data')

In [0]:
df_pred_joined = df_pred_cluster.join(df_popularity.select('song_id','prediction','title','artist_name')\
                              .withColumnRenamed('prediction','popularity_prediction'),'song_id',how='inner')
df_pred_joined.display()

song_id user_id prediction song_feature popularity_prediction title artist_name SOXPFLM12A8AE48C50 d8e6fa08d73821f305b9a3af1cf1e0a704473d82 56 Map(vectorType -> dense, length -> 10, values -> List(0.0710303479698813, 0.8546374563104029, -0.2567378910388916, 0.1625837852502135, -0.08350840156340296, 0.16996427517455476, 0.1468859752818088, -0.14591144777502224, -0.4206632702035984, -0.66742895340108)) 0.9172673404463499 Electric Feel MGMT SOJDOJC12A8AE46372 ffad6a9352f87dbe61482e8a7dbb1bf8cf37c8be 95 Map(vectorType -> dense, length -> 10, values -> List(0.5276774651925974, 0.343930806117979, -0.2423657561567697, -0.05013949766454071, -0.038228259205517146, 0.07489163989220003, 0.12798837734141735, -0.21172634956210554, -0.37032475060962067, -0.28907794563683)) 0.8431346350742054 Gravity John Mayer SOJDOJC12A8AE46372 ffad6a9352f87dbe61482e8a7dbb1bf8cf37c8be 95 Map(vectorType -> dense, length -> 10, values -> List(0.5276774651925974, 0.343930806117979, -0.2423657561567697, -0.05013949766454071, -0.038228259205517146, 0.07489163989220003, 0.12798837734141735, -0.21172634956210554, -0.37032475060962067, -0.28907794563683)) 0.8431346350742054 Gravity John Mayer SOLWZVR12AB01849C6 d8e6fa08d73821f305b9a3af1cf1e0a704473d82 46 Map(vectorType -> dense, length -> 10, values -> List(0.0710303479698813, 0.8546374563104029, -0.2567378910388916, 0.1625837852502135, -0.08350840156340296, 0.16996427517455476, 0.1468859752818088, -0.14591144777502224, -0.4206632702035984, -0.66742895340108)) 1.0 All The Right Moves OneRepublic SOUJVIT12A8C1451C1 d8e6fa08d73821f305b9a3af1cf1e0a704473d82 52 Map(vectorType -> dense, length -> 10, values -> List(0.0710303479698813, 0.8546374563104029, -0.2567378910388916, 0.1625837852502135, -0.08350840156340296, 0.16996427517455476, 0.1468859752818088, -0.14591144777502224, -0.4206632702035984, -0.66742895340108)) 0.9181823430861558 Savior Rise Against SOUJVIT12A8C1451C1 5a44bfcaa1081e8b36ff76ec32c2ef73425ad2e9 52 Map(vectorType -> dense, length -> 10, values -> List(0.3575763726385973, 0.3424021452665329, -0.2032273274735879, 0.03900779788461277, -0.10597101838911994, 0.03925409376368684, 0.010823265980865996, -0.11968894927936086, -0.3572702215889753, -0.2654513599256338)) 0.9181823430861558 Savior Rise Against SOMRMKA12AF72A0867 42b31eaf0cbaa10e593438e2858ce74cdfa01191 25 Map(vectorType -> dense, length -> 10, values -> List(0.2847496314561941, 0.3727896250186757, -0.22092986174107074, -0.16174896910069458, -9.667311600822815E-4, -0.07954941303494142, -0.09612808097651936, -0.23230006213095736, -0.3542167611300626, -0.4664711772917426)) 0.8605974167434027 Fire Bomb Rihanna SORNJET12A8C1415A8 ca9fb6d60f3261f783936a7ff48df2df176d5b3a 70 Map(vectorType -> dense, length -> 10, values -> List(0.3057208630429991, 0.36509900067348855, -0.2704815409951291, 0.08274208154466192, -0.10478010697890136, -0.042455501317725346, 0.16422455688401805, -0.27552172472163783, -0.4417423092902212, -0.5421508339123201)) 0.9279181169504825 Sky And Sand Paul & Fritz Kalkbrenner SORNJET12A8C1415A8 8665ae2a21ff60a45bf638c941a61a0cb75d7687 70 Map(vectorType -> dense, length -> 10, values -> List(0.5631643886799398, 0.461445778068425, -0.18066169661672218, -0.05995848573798287, 0.19475149438864944, -0.0735933605203594, 0.02287291357482689, -0.24515994972940805, -0.2565212040275767, -0.5326204021879728)) 0.9279181169504825 Sky And Sand Paul & Fritz Kalkbrenner SOSROFB12AAF3B4C5D d8e6fa08d73821f305b9a3af1cf1e0a704473d82 35 Map(vectorType -> dense, length -> 10, values -> List(0.0710303479698813, 0.8546374563104029, -0.2567378910388916, 0.1625837852502135, -0.08350840156340296, 0.16996427517455476, 0.1468859752818088, -0.14591144777502224, -0.4206632702035984, -0.66742895340108)) 1.0 You Belong With Me Taylor Swift SOSROFB12AAF3B4C5D 7d068212c72cc9bc67ebfcabb93c5ace75b78bee 35 Map(vectorType -> dense, length -> 10, values -> List(0.41815547065602404, 0.2039281390607357, 0.025319878839784198, -0.0683475641740693, 0.3856891393661499, -0.35117893

In [0]:
df_pred_joined.createOrReplaceTempView('pred_joined')

In [0]:
df_merged_pop_kmeans = spark.sql('select * from (select user_id,song_id,title, artist_name, prediction, popularity_prediction, rank() over(partition by prediction order by popularity_prediction desc) as song_rank from pred_joined) ranked where song_rank<= 5')
df_merged_pop_kmeans.display()

user_id song_id title artist_name prediction popularity_prediction song_rank 5a44bfcaa1081e8b36ff76ec32c2ef73425ad2e9 SOTXDCY12AF729A39B Drunken Lullabies Flogging Molly 0 0.8934375438630937 1 af8b6cf5ad80a0f5696192586824783a49c29805 SOKBWGX12AB0187497 Sea of lies Symphony X 0 0.7833053169999009 2 ca9fb6d60f3261f783936a7ff48df2df176d5b3a SOROWQE12A81C206ED The Chamber The Last Shadow Puppets 0 0.7184041679497776 3 c53ac12f0b9396ab3f44f7b521d5925b10e991d3 SOISNQR12A8C136E83 Quero te Amar Bonde Do Role 1 0.5422378246522243 1 ca9fb6d60f3261f783936a7ff48df2df176d5b3a SOGSCTA12A6D4FBE69 S-Bahn-Surfen (2007 Digital Remaster) Spider Murphy Gang 1 0.0 2 42b31eaf0cbaa10e593438e2858ce74cdfa01191 SOTPERU12A6D4F9358 Jogging Yelle 2 0.6604177743630324 1 6c966bdfc8ef4699fe1814e18573419b725d94e6 SOWBYZF12A6D4F9424 Fakty Horkyze Slyze 2 0.41845804751567073 2 296e5769223ae111e530d96c8bcf95fd63d8af9b SOSXPFU12AB017FE27 The Calculation (Album Version) Regina Spektor 3 0.8428184693316623 1 ffad6a9352f87dbe61482e8a7dbb1bf8cf37c8be SOSJRXV12A8C136E1B Everything Is Everything Lauryn Hill 3 0.7718617483179527 2 78d77cba6776c72ca78a52aa66f2526eabd86ea7 SOULBNJ12AB01851E9 240 Years Before Your Time The Black Keys 3 0.7061678552383803 3 f46ea20e521fac56af45e37bd02a5cfd1c444b6e SOCLSPA12A6D4F705C Living On My Own (Radio Mix) (2000 Digital Remaster) Freddie Mercury 3 0.6769698926584398 4 ca9fb6d60f3261f783936a7ff48df2df176d5b3a SOJQPOH12A6D4FB1AB Dom / Hollow [Live Version] Pantera 3 0.6012170574855539 5 5a44bfcaa1081e8b36ff76ec32c2ef73425ad2e9 SOGTEVT12AF72A4D11 The Preacher NITIN SAWHNEY 4 0.6465982542053272 1 f0eb3676a2b775f67f3e6ddc3ad43006f50d4aca SOIVZJE12A8C13D9D8 Martyrdom Unsealed Job For A Cowboy 4 0.6399045780708916 2 78d77cba6776c72ca78a52aa66f2526eabd86ea7 SOVASUH12A67021B44 Midnight Lightning Jimi Hendrix 4 0.5823442861044243 3 78d77cba6776c72ca78a52aa66f2526eabd86ea7 SOVASUH12A67021B44 Midnight Lightning Jimi Hendrix 4 0.5823442861044243 3 78d77cba6776c72ca78a52aa66f2526eabd86ea7 SOVASUH12A67021B44 Midnight Lightning Jimi Hendrix 4 0.5823442861044243 3 78d77cba6776c72ca78a52aa66f2526eabd86ea7 SOVASUH12A67021B44 Midnight Lightning Jimi Hendrix 4 0.5823442861044243 3 78d77cba6776c72ca78a52aa66f2526eabd86ea7 SOVASUH12A67021B44 Midnight Lightning Jimi Hendrix 4 0.5823442861044243 3 78d77cba6776c72ca78a52aa66f2526eabd86ea7 SOVASUH12A67021B44 Midnight Lightning Jimi Hendrix 4 0.5823442861044243 3 78d77cba6776c72ca78a52aa66f2526eabd86ea7 SOVASUH12A67021B44 Midnight Lightning Jimi Hendrix 4 0.5823442861044243 3 78d77cba6776c72ca78a52aa66f2526eabd86ea7 SOVASUH12A67021B44 Midnight Lightning Jimi Hendrix 4 0.5823442861044243 3 78d77cba6776c72ca78a52aa66f2526eabd86ea7 SOVASUH12A67021B44 Midnight Lightning Jimi Hendrix 4 0.5823442861044243 3 ca9fb6d60f3261f783936a7ff48df2df176d5b3a SOVRTPN12AB0184F9E Howlin For You The Black Keys 5 1.0 1 42b31eaf0cbaa10e593438e2858ce74cdfa01191 SOXVXDS12AF72A4704 Mal Poli Yelle 5 0.8366246879979944 2 f0eb3676a2b775f67f3e6ddc3ad43006f50d4aca SOIYNKK12A6D4F7A54 Esse Coracao (Este Corazón) RBD 5 0.7966929516579855 3 42b31eaf0cbaa10e593438e2858ce74cdfa01191 SOZPQXP12A8C1301ED Ce Jeu Yelle 5 0.7465996488015103 4 5a44bfcaa1081e8b36ff76ec32c2ef73425ad2e9 SOGNNDB12A8C13C0A0 J'Suis Pas D'Ici Thomas Dutronc 5 0.6297622253437221 5 f46ea20e521fac56af45e37bd02a5cfd1c444b6e SOQHFWA12AAA8C6662 Engel Rammstein 6 0.7515342560256725 1 f46ea20e521fac56af45e37bd02a5cfd1c444b6e SOLIJXB12A8C13F529 Keine Lust Rammstein 6 0.7234958611058167 2 5a44bfcaa1081e8b36ff76ec32c2ef73425ad2e9 SOWEJXA12A6701C574 Fix You Coldplay 7 1.0 1 98cb9a3feb48d15a8328ce16f1b32609698e11f2 SOSVPIE12A6D4FA873 Shiver Coldplay 7 0.8649306047264143 2 78d77cba6776c72ca78a52aa66f2526eabd86ea7 SOVOLWT12A8C132DA5 Hold On Kansas 7 0.8251420463419232 3 d8e6fa08d73821f305b9a3af1cf1e0a704473d82 SOPYOCU12AB017A91B Set Down Your Glass Snow Patrol 7 0.7668009929485463 4 d8e6fa08d73821f305b9a3af1cf1e0a704473d82 SOPYOCU12AB017A91B Set Down Your Glass Snow Patrol 7 0.7668009929485463

In [0]:
df_final = df_pred_joined.withColumnRenamed('song_id','original_song_id').select('original_song_id','prediction').join(df_merged_pop_kmeans,'prediction',how='left')
df_final.display()

prediction original_song_id user_id song_id title artist_name popularity_prediction song_rank 85 SODXHYV12A8C13AE0A 78d77cba6776c72ca78a52aa66f2526eabd86ea7 SODXHYV12A8C13AE0A Nur Ein Wort (Berlin-Town) (P.R. Kantate & Meine Band Version) Wir Sind Helden 0.3725300393660796 2 85 SODXHYV12A8C13AE0A 42b31eaf0cbaa10e593438e2858ce74cdfa01191 SOMKYIZ12A8C141413 Nothing's Lost Patrick Park 0.5734431930798345 1 78 SOYYJMW12A6D4F8636 6a145b64e3f73ea3018ed88c790c0804c2176ccd SOYYJMW12A6D4F8636 Hands Open Snow Patrol 0.8374948160050059 5 78 SOYYJMW12A6D4F8636 6c966bdfc8ef4699fe1814e18573419b725d94e6 SOBTRCD12A6701E976 Where Did You Sleep Last Night Nirvana 0.8762736368731534 4 78 SOYYJMW12A6D4F8636 ffad6a9352f87dbe61482e8a7dbb1bf8cf37c8be SOXWYZP12AF72A42A6 Cosmic Love Florence + The Machine 0.9161084532792769 1 78 SOYYJMW12A6D4F8636 d8e6fa08d73821f305b9a3af1cf1e0a704473d82 SOXWYZP12AF72A42A6 Cosmic Love Florence + The Machine 0.9161084532792769 1 78 SOYYJMW12A6D4F8636 7d068212c72cc9bc67ebfcabb93c5ace75b78bee SOXWYZP12AF72A42A6 Cosmic Love Florence + The Machine 0.9161084532792769 1 78 SOBTRCD12A6701E976 6a145b64e3f73ea3018ed88c790c0804c2176ccd SOYYJMW12A6D4F8636 Hands Open Snow Patrol 0.8374948160050059 5 78 SOBTRCD12A6701E976 6c966bdfc8ef4699fe1814e18573419b725d94e6 SOBTRCD12A6701E976 Where Did You Sleep Last Night Nirvana 0.8762736368731534 4 78 SOBTRCD12A6701E976 ffad6a9352f87dbe61482e8a7dbb1bf8cf37c8be SOXWYZP12AF72A42A6 Cosmic Love Florence + The Machine 0.9161084532792769 1 78 SOBTRCD12A6701E976 d8e6fa08d73821f305b9a3af1cf1e0a704473d82 SOXWYZP12AF72A42A6 Cosmic Love Florence + The Machine 0.9161084532792769 1 78 SOBTRCD12A6701E976 7d068212c72cc9bc67ebfcabb93c5ace75b78bee SOXWYZP12AF72A42A6 Cosmic Love Florence + The Machine 0.9161084532792769 1 34 SOJTIXE12AB018C99E d8e6fa08d73821f305b9a3af1cf1e0a704473d82 SONIQRE12AF72A2B02 Bring Me To Life Evanescence 1.0 1 34 SOJTIXE12AB018C99E 6c966bdfc8ef4699fe1814e18573419b725d94e6 SONIQRE12AF72A2B02 Bring Me To Life Evanescence 1.0 1 34 SOJTIXE12AB018C99E d8e6fa08d73821f305b9a3af1cf1e0a704473d82 SONIQRE12AF72A2B02 Bring Me To Life Evanescence 1.0 1 34 SOJTIXE12AB018C99E 6c966bdfc8ef4699fe1814e18573419b725d94e6 SONIQRE12AF72A2B02 Bring Me To Life Evanescence 1.0 1 34 SOJTIXE12AB018C99E d8e6fa08d73821f305b9a3af1cf1e0a704473d82 SONIQRE12AF72A2B02 Bring Me To Life Evanescence 1.0 1 34 SOJTIXE12AB018C99E 6c966bdfc8ef4699fe1814e18573419b725d94e6 SONIQRE12AF72A2B02 Bring Me To Life Evanescence 1.0 1 34 SOJTIXE12AB018C99E d8e6fa08d73821f305b9a3af1cf1e0a704473d82 SONIQRE12AF72A2B02 Bring Me To Life Evanescence 1.0 1 34 SOJTIXE12AB018C99E 6c966bdfc8ef4699fe1814e18573419b725d94e6 SONIQRE12AF72A2B02 Bring Me To Life Evanescence 1.0 1 34 SOXWHOW12A8C13D3F6 d8e6fa08d73821f305b9a3af1cf1e0a704473d82 SONIQRE12AF72A2B02 Bring Me To Life Evanescence 1.0 1 34 SOXWHOW12A8C13D3F6 6c966bdfc8ef4699fe1814e18573419b725d94e6 SONIQRE12AF72A2B02 Bring Me To Life Evanescence 1.0 1 34 SOXWHOW12A8C13D3F6 d8e6fa08d73821f305b9a3af1cf1e0a704473d82 SONIQRE12AF72A2B02 Bring Me To Life Evanescence 1.0 1 34 SOXWHOW12A8C13D3F6 6c966bdfc8ef4699fe1814e18573419b725d94e6 SONIQRE12AF72A2B02 Bring Me To Life Evanescence 1.0 1 34 SOXWHOW12A8C13D3F6 d8e6fa08d73821f305b9a3af1cf1e0a704473d82 SONIQRE12AF72A2B02 Bring Me To Life Evanescence 1.0 1 34 SOXWHOW12A8C13D3F6 6c966bdfc8ef4699fe1814e18573419b725d94e6 SONIQRE12AF72A2B02 Bring Me To Life Evanescence 1.0 1 34 SOXWHOW12A8C13D3F6 d8e6fa08d73821f305b9a3af1cf1e0a704473d82 SONIQRE12AF72A2B02 Bring Me To Life Evanescence 1.0 1 34 SOXWHOW12A8C13D3F6 6c966bdfc8ef4699fe1814e18573419b725d94e6 SONIQRE12AF72A2B02 Bring Me To Life Evanescence 1.0 1 34 SOADJQJ12A8C141D38 d8e6fa08d73821f305b9a3af1cf1e0a704473d82 SONIQRE12AF72A2B02 Bring Me To Life Evanescence 1.0 1 34 SOADJQJ12A8C141D38 6c966bdfc8ef4699fe1814e18573419b725d94e6 SONIQRE12AF72A2B02 Bring Me To Life Evanescence 1.0 1 34 SOADJQJ12A8C141D38 d8e6fa08d73821f305b9a3af1cf1e0a704473d82 SONIQRE12AF72A2B02 Bring Me To Life Evanescence 1.0 1 34 SOA

In [0]:
#Saving final table
df_final.write.mode("overwrite").saveAsTable("default.lyrics_final")